In [1]:
import pandas as pd
import geopandas as gpd
import folium

from shapely.geometry import Point, Polygon

from pathlib import Path
root = Path.cwd()

### Beech points from DEP

In [16]:
pts_1 = gpd.read_file(root / 'catskills' / 'beech_points1.shp')
pts_2 = gpd.read_file(root / 'catskills' / 'beech_points2.shp')
pts_3 = gpd.read_file(root / 'catskills' / 'beech_points3.shp')

In [17]:
all_pts = pd.concat([pts_1,pts_2,pts_3])
beech_pts = all_pts.loc[all_pts['Comment']=='Beech',['Comment','geometry']]
nonbeech_pts = all_pts.loc[all_pts['Comment']!='Beech',['Comment','geometry']]


### DEP Inventory Plots

In [2]:
inv_plots = gpd.read_file(root / 'catskills' / 'All_Inventory_Plots.shp')
tab_data = pd.read_excel(root / 'catskills' / 'OverstoryObs_Combined_Kingston.xlsx')
tab_data = tab_data.loc[tab_data['YEAR']!=2009,:]

In [20]:
inv_plots.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 12403 entries, 0 to 12402
Data columns (total 5 columns):
 #   Column      Non-Null Count  Dtype   
---  ------      --------------  -----   
 0   PlotID      12403 non-null  object  
 1   Basin       3025 non-null   object  
 2   subbasin1m  12403 non-null  object  
 3   STAND_ID    3025 non-null   object  
 4   geometry    12403 non-null  geometry
dtypes: geometry(1), object(4)
memory usage: 484.6+ KB


In [19]:
tab_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 35927 entries, 0 to 147005
Data columns (total 19 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   TreeID_orig   35927 non-null  int64  
 1   PlotID_orig   35927 non-null  object 
 2   TreeID_new    35927 non-null  int64  
 3   StandID       35927 non-null  int64  
 4   PlotID_new    35927 non-null  int64  
 5   OverID        35927 non-null  int64  
 6   USDA_CODE     35887 non-null  object 
 7   DBH           35927 non-null  int64  
 8   DEAD          35927 non-null  int64  
 9   CROWN_CLASS   32973 non-null  object 
 10  AGS           35927 non-null  int64  
 11  HEALTH        9652 non-null   object 
 12  PRODUCT       35887 non-null  object 
 13  SURVEY        35927 non-null  object 
 14  YEAR          35927 non-null  int64  
 15  SPECIES_NAME  35887 non-null  object 
 16  TreeBA        35927 non-null  float64
 17  TPA/EF        35927 non-null  float64
 18  Size Class    35887 non-null  

In [ ]:
any(inv_plots['PlotID'].isin(tab_data['PlotID_orig']))

False

In [18]:
m = folium.Map(location=(44,-74), zoom_start=5)

folium.GeoJson(
    beech_pts.to_crs(4326),
    marker=folium.Circle(radius=2, fill_color="red", fill_opacity=0.4, color="red", weight=1),
    tooltip=folium.GeoJsonTooltip(fields=['Comment'])
).add_to(m)

folium.GeoJson(
    nonbeech_pts.to_crs(4326),
    marker=folium.Circle(radius=2, fill_color="blue", fill_opacity=0.4, color="blue", weight=1),
    tooltip=folium.GeoJsonTooltip(fields=['Comment'])
).add_to(m)

folium.GeoJson(
    inv_plots.to_crs(4326),
    marker=folium.Circle(radius=2, fill_color="blue", fill_opacity=0.4, color="blue", weight=1),
    tooltip=folium.GeoJsonTooltip(fields=['PlotID'])
).add_to(m)

m

### Catskills polygons from Justin

In [2]:
pts = gpd.read_file(root / 'beech_stands' / 'Points.shp' )
pts = pts.to_crs(26918)
# remove first 4 rows
pts2 = pts.loc[4:,].copy()

# make separate species and dbh columns
pts2['species'] = [x[0] for x in pts2.Name.str.split('dbh')]
pts2['dbh'] = [x[-1] for x in pts2.Name.str.split('dbh')]
pts2 = pts2.drop('Name',axis=1)

# make separate beech and nonbeech gdf
pts2['species'] = pts2.species.str.strip()
pts2['dbh'] = pts2['dbh'].str.strip()

pts2 = pts2[['geometry','species','dbh','Desc']]
# beech_pts = pts2.loc[pts2.species=='beech'].copy()
# beech_pts.shape
# beech_pts['index'] = np.arange(0,len(beech_pts))

# nonbeech_pts = pts2.loc[pts2.species!='beech'].copy()
# nonbeech_pts.shape
# nonbeech_pts = nonbeech_pts.reset_index()

# define 100m buffers for each cluster of pointss
# pecoy_buffer = beech_pts.iloc[27:28,].copy().buffer(100)
# roundtop_buffer = beech_pts.iloc[54:55,].copy().buffer(100)
# visitors_buffer = beech_pts.iloc[66:67,].copy().buffer(100)

# polys = gpd.read_file(root / 'beech_stands' / 'Beech Stand Polygons.kml')
# polys = polys.reset_index()

In [3]:
#pts2.loc[pts2['species'].isin(['hemlock 51.6','red spruce 29.5','2x 30+','beech 37.9'])]

# manually clean species/dbh columns bc there aren't that many

pts2.loc[pts2['species']=='hemlock 51.6','dbh'] = 52
pts2.loc[pts2['species']=='hemlock 51.6','species'] = 'hemlock'

pts2.loc[pts2['species']=='red spruce 29.5','dbh'] = 30
pts2.loc[pts2['species']=='red spruce 29.5','species'] = 'spruce'

pts2.loc[pts2['species']=='2x 30+','dbh'] = 30
pts2.loc[pts2['species']=='2x 30+','species'] = 'beech'

pts2.loc[pts2['species']=='beech 37.9','dbh'] = 38
pts2.loc[pts2['species']=='beech 37.9','species'] = 'beech'

pts2.loc[pts2['species']=='sugar mappe','species'] = 'maple'
pts2.loc[pts2['species']=='sugar maple','species'] = 'maple'

pts2.loc[pts2['species']=='paper birch','species'] = 'birch'

### dbh
#pts2.loc[pts2['dbh'].str.contains('|'.join(['stem','snag']),na=False)]
pts2.loc[pts2['dbh']=='36.7 2nd stem 22.4','dbh'] = 36.7 + 22.4

pts2.loc[pts2['dbh']=='21.5 2nd stem 12.3','dbh'] = 21.5 + 12.3

pts2.loc[pts2['dbh']=='40.9 second stem 29.7','dbh'] = 40.9 + 29.7

pts2.loc[pts2['dbh']=='36.6 2nd stem 33.2','dbh'] = 36.6 + 33.2

pts2.loc[pts2['dbh']=='44.6 2nd stem 31','dbh'] = 44.6 + 31

pts2.loc[pts2['dbh']=='','dbh'] = 37.2
pts2.loc[pts2['dbh']=='36.5 snag','dbh'] = 36.5
pts2.loc[pts2['dbh']=='45 snag','dbh'] = 45

pts2['dbh'] = pts2['dbh'].astype('float')

pts2['dbh_inches'] = pts2['dbh'] / 2.54

### create taxonID column
tree_dict = {'hemlock':261,'maple':316,'beech':531,'birch':371,'oak':833,'spruce':91,'unknown':999}

pts2['taxonID'] = pts2['species'].map(tree_dict).fillna(999)


### filter out dead trees
# 0 = dead or fallen
# 1 = disease
# 2 = living
desc_dict = {'dead':0,'dead now':0,'heavy scale and neonectria': 1, 'stem and crown arch sourheast. heavy scale and neonectria':1,'fork stem one dead one alive':2,'fallen but probably standing at date of aviris':0,'non stand indovidual':2,'non stand indovidual-dead':0,'crown snapped':0,'fallen':0,'no BBD!':2,'dead and fallen half missing on dbh':2,'touching similar sized sugar maple':2,'thick beech understroy':2,'fallen leaner':0,'37.2':2,'very large canopy, many smaller beech in stand but all much you ger, sub 30 dbh':2}

pts2['Desc'] = pts2['Desc'].str.strip()

pts2['status'] = pts2['Desc'].map(desc_dict).fillna(2)

pts2 = pts2.loc[pts2['status']!=0.0]

In [4]:
pts2['taxonID'].value_counts()

taxonID
531.0    71
261.0     5
833.0     2
371.0     1
316.0     1
91.0      1
999.0     1
Name: count, dtype: int64

In [ ]:
pts2.to_file(root / 'output' / 'CATSKILLS' / 'all_trees_CATSKILLS.gpkg')

In [ ]:
import math

def get_point_at_distance(easting,northing,bearing,distance):
    bearing_rad = math.radians(bearing)

    # Calculate the change in easting and northing
    delta_easting = distance * math.sin(bearing_rad)
    delta_northing = distance * math.cos(bearing_rad)

    # Calculate the new coordinates
    easting_new = easting + delta_easting
    northing_new = northing + delta_northing

    return Point(easting_new, northing_new)

#bearings:
south = 180
west = 270
east = 90
sw = 225
nw = 315
se = 135
ne = 45

# create smaller area of interest
#ref_point = nonbeech_pts.loc[nonbeech_pts['index']==54]['geometry']  # select reference point
ref_point = beech_pts.loc[beech_pts['index']==57]['geometry'] 
easting = ref_point.x
northing = ref_point.y
ref_point = Point(easting,northing)

ref_point = get_point_at_distance(easting,northing,east,1000)
easting = ref_point.x
northing = ref_point.y
ref_point = Point(easting,northing)


distance = 21000
p1 = get_point_at_distance(easting,northing,south,distance)

p2 = get_point_at_distance(easting,northing,west,distance)
distance = np.sqrt((distance**2)*2) # hypotenuse
p3 = get_point_at_distance(easting,northing,sw,distance)

p2a = get_point_at_distance(p2.x,p2.y,east,5500)
p3a = get_point_at_distance(p3.x,p3.y,east,5500)

newpoints = gpd.GeoDataFrame({'point':['p0','p1','p2','p3'],'geometry':[ref_point,p1,p2a,p3a]},crs=26918)

In [ ]:
new_polys = gpd.read_file(root / 'beech_stands' / 'Beech ground truth polygons' / 'BeechGroundTruthingPolygons_ExportFeatures.shp')

In [ ]:
polys['beech_basal_area'] = [100,100,100,100,0,0,0,0]

polys = polys[['geometry','beech_basal_area']]
new_polys = new_polys[['geometry','beech_basal_area']]

all_polys = pd.concat([polys,new_polys],axis=0)
all_polys

all_polys = all_polys.to_crs(26918)

all_polys.to_file(root / 'output' / 'CATSKILLS' / 'all_trees_CATSKILLS.gpkg')

new_polys['beech_basal_area'] = [0,80,60,0,80,80,0,20,0,60]
new_polys

In [4]:
# choose point to serve as map center coordinates
map_coords = tuple(pts2.to_crs(4326).get_coordinates().iloc[37,]) # get xy coords for index 37
map_coords = tuple([map_coords[1],map_coords[0]]) # switch them around because everything is integrated seamlessly

# define 100m buffers for each cluster of pointss
# pecoy_buffer = beech_pts.iloc[27:28,].buffer(100)
# roundtop_buffer = beech_pts.iloc[54:55,].buffer(100)
# visitors_buffer = beech_pts.iloc[66:67,].buffer(100)

# s = pd.concat([pecoy_buffer,roundtop_buffer,visitors_buffer])

# plot results
m = folium.Map(location=map_coords, zoom_start=11)

folium.GeoJson(
    pts2.to_crs(4326),
    marker=folium.Circle(radius=2, fill_color="orange", fill_opacity=0.4, color="orange", weight=1),
    tooltip=folium.GeoJsonTooltip(fields=["species",'Desc'])
).add_to(m)

# folium.GeoJson(
#     nonbeech_pts.to_crs(4326),
#     marker=folium.Circle(radius=2, fill_color="red", fill_opacity=0.4, color="red", weight=1),
#     tooltip=folium.GeoJsonTooltip(fields=["index","species"])
# ).add_to(m)

# # add buffers to map
# folium.GeoJson(
#     newpoints.to_crs(4326)
# ).add_to(m)

# folium.GeoJson(
#     new_polys.to_crs(4326),
#     style_function=lambda x:{
#         "fillColor": "blue"
#         if x["properties"]["Name"] != 'Beech'
#         else "green",
#         "color": "blue"
#         if x["properties"]["Name"] != 'Beech'
#         else "green"
#         }
# ).add_to(m)

# folium.GeoJson(
#     polys,
#     style_function=lambda x:{
#          "fillColor": "red"
#         if x['properties']["Name"] == 'non-beech stand'
#         else "orange",
#         "color":"red"
#         if x['properties']["Name"] == 'non-beech stand'
#         else "orange"},
#     tooltip=folium.GeoJsonTooltip(fields=["Name","index"])
# ).add_to(m)

m

In [ ]:
m.save(root / 'figures' / 'catskills.html')